# Datos ciudad de Barcelona

https://opendata-ajuntament.barcelona.cat/data/es/dataset/transports/resource/e07dec0d-4aeb-40f3-b987-e1f35e088ce2

In [2]:
import xml.etree.ElementTree as et
import pandas as pd
import numpy as np

## Metro Data

In [2]:
file = 'TRANSPORTS_barcelona2.csv'

In [3]:
metro_bar_stations = pd.read_csv(file)

In [4]:
metro_bar_stations.head()

CODI_CAPA                     CAPA_GENERICA                        NOM_CAPA  \
0      K001  Transports i serveis relacionats      Metro i línies urbanes FGC   
1      K002  Transports i serveis relacionats  Ferrocarrils Generalitat (FGC)   
2      K001  Transports i serveis relacionats      Metro i línies urbanes FGC   
3      K001  Transports i serveis relacionats      Metro i línies urbanes FGC   
4      K001  Transports i serveis relacionats      Metro i línies urbanes FGC   

   ED50_COORD_X  ED50_COORD_Y  ETRS89_COORD_X  ETRS89_COORD_Y  LONGITUD  \
0    428480.365   4586484.614      428388.453     4586283.641  2.142987   
1    429726.943   4582853.670      429635.018     4582652.730  2.158326   
2    426477.889   4583649.008      426385.994     4583448.062  2.119370   
3    427818.595   4583478.761      427726.688     4583277.816  2.135427   
4    432051.444   4589400.176      431959.500     4589199.175  2.185391   

     LATITUD                                         EQUIPAMENT  DISTRICTE  \
0  41.424923  METRO (L3, L5) - VALL D'HEBRON (C. de les Bass...        7.0   
1  41.392331                   FGC - PROVENÇA (C. de Provença)-        2.0   
2  41.399203  FGC (L6) - REINA ELISENDA (Sortida Duquesa d'O...        5.0   
3  41.397791                            FGC (L6) - LA BONANOVA-        5.0   
4  41.451492      METRO (L11) - CASA DE L'AIGUA (C. Vila-Real)-        8.0   

   BARRI        NOM_DISTRICTE                        NOM_BARRI ADRECA TELEFON  
0   41.0       Horta-Guinardó                 la Vall d'Hebron    NaN     NaN  
1    8.0             Eixample  l'Antiga Esquerra de l'Eixample    NaN     NaN  
2   23.0  Sarrià-Sant Gervasi                           Sarrià    NaN     NaN  
3   26.0  Sarrià-Sant Gervasi           Sant Gervasi - Galvany    NaN     NaN  
4   53.0           Nou Barris                 la Trinitat Nova    NaN     NaN

In [5]:
metro_bar_stations = metro_bar_stations[['EQUIPAMENT','NOM_BARRI','LONGITUD','LATITUD']]\
    .rename(columns={'LONGITUD':'Longitude','LATITUD':'Latitude'})
    
metro_bar_stations.to_csv('metro_barcelona.csv')

### Open data

In [3]:
barcelona_stations = pd.read_csv('metro_barcelona.csv', index_col=0)
print('barcelona stations shape', barcelona_stations.shape)

barcelona stations shape (651, 4)


In [4]:
## Getting the info of station and line
barcelona_stations['line'] = barcelona_stations['EQUIPAMENT'].apply(lambda x: x.split('-')[0].strip())
barcelona_stations.head()

EQUIPAMENT  \
0  METRO (L3, L5) - VALL D'HEBRON (C. de les Bass...   
1                   FGC - PROVENÇA (C. de Provença)-   
2  FGC (L6) - REINA ELISENDA (Sortida Duquesa d'O...   
3                            FGC (L6) - LA BONANOVA-   
4      METRO (L11) - CASA DE L'AIGUA (C. Vila-Real)-   

                         NOM_BARRI  Longitude   Latitude            line  
0                 la Vall d'Hebron   2.142987  41.424923  METRO (L3, L5)  
1  l'Antiga Esquerra de l'Eixample   2.158326  41.392331             FGC  
2                           Sarrià   2.119370  41.399203        FGC (L6)  
3           Sant Gervasi - Galvany   2.135427  41.397791        FGC (L6)  
4                 la Trinitat Nova   2.185391  41.451492     METRO (L11)

In [5]:
## Getting the info of station
barcelona_stations['station'] = barcelona_stations['EQUIPAMENT'].apply(lambda x: x.split('-'))\
                    .apply(lambda x: x[1] if len(x)>1 else x[0])\
                    .apply(lambda x: x.split('(')[0].strip())
barcelona_stations.head()

EQUIPAMENT  \
0  METRO (L3, L5) - VALL D'HEBRON (C. de les Bass...   
1                   FGC - PROVENÇA (C. de Provença)-   
2  FGC (L6) - REINA ELISENDA (Sortida Duquesa d'O...   
3                            FGC (L6) - LA BONANOVA-   
4      METRO (L11) - CASA DE L'AIGUA (C. Vila-Real)-   

                         NOM_BARRI  Longitude   Latitude            line  \
0                 la Vall d'Hebron   2.142987  41.424923  METRO (L3, L5)   
1  l'Antiga Esquerra de l'Eixample   2.158326  41.392331             FGC   
2                           Sarrià   2.119370  41.399203        FGC (L6)   
3           Sant Gervasi - Galvany   2.135427  41.397791        FGC (L6)   
4                 la Trinitat Nova   2.185391  41.451492     METRO (L11)   

           station  
0    VALL D'HEBRON  
1         PROVENÇA  
2   REINA ELISENDA  
3      LA BONANOVA  
4  CASA DE L'AIGUA

In [6]:
barcelona_stations['station'].unique().shape

(230,)

In [7]:
## Remove duplicate stations
barcelona_stations.drop_duplicates(subset ="station", 
                     keep = 'first', inplace=True)
print('Barcelona unique stations', barcelona_stations.shape)

Barcelona unique stations (230, 6)


### Save data and open

In [8]:
# save
barcelona_stations.to_csv('metro_barcelona_uniques.csv')

In [9]:
# open
barcelona_stations = pd.read_csv('metro_barcelona_uniques.csv', index_col=0)

## Show map stations

In [11]:
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors
import folium

mapi = folium.Map(location=[barcelona_stations.Latitude.mean(), barcelona_stations.Longitude.mean()], 
                  zoom_start=12,
                  control_scale = True)
folium.TileLayer('cartodbpositron', attr='igs').add_to(mapi)

# set color scheme for the clusters
n = len(barcelona_stations['line'].unique())
x = np.arange(n)
perro = dict(zip(barcelona_stations['line'].unique(),x))
ys = [i + x + (i*x)**2 for i in range(n)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]



# add markers to the map
markers_colors = []
for lat, lon, poi, line in zip(barcelona_stations['Latitude'], 
                                  barcelona_stations['Longitude'], 
                                  barcelona_stations['station'], 
                                  barcelona_stations['line']):
    label = folium.Popup(str(poi) + ' Line ' + str(line), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=2,
        popup=label,
        color=rainbow[perro[line]-1],
        fill=True,
        fill_color=rainbow[int(perro[line])-1],
        fill_opacity=0.7).add_to(mapi)
       
mapi

# Neighborhoods

BCN_UNITATS_ADM/0301040100_Barris_ADM_ETRS89.shp

In [12]:
import geopandas as gp

In [13]:
neighboorhoods = gp.read_file('BCN_UNITATS_ADM/0301040100_Barris_ADM_ETRS89.shp')

In [14]:
print(neighboorhoods.shape)
neighboorhoods.head()

(73, 47)


ID_ANNEX ANNEXDESCR ID_TEMA               TEMA_DESCR ID_CONJUNT CONJ_DESCR  \
0       01   Grup - I    0104  Unitats Administratives     010413     Barris   
1       01   Grup - I    0104  Unitats Administratives     010413     Barris   
2       01   Grup - I    0104  Unitats Administratives     010413     Barris   
3       01   Grup - I    0104  Unitats Administratives     010413     Barris   
4       01   Grup - I    0104  Unitats Administratives     010413     Barris   

  ID_SUBCONJ SCONJ_DESC  ID_ELEMENT       ELEM_DESCR  ... ESTIL_ID ESTIL_QGIS  \
0   01041301      Barri  0104130101  LÃ­mit de barri  ...        0     SÃ²lid   
1   01041301      Barri  0104130101  LÃ­mit de barri  ...        0     SÃ²lid   
2   01041301      Barri  0104130101  LÃ­mit de barri  ...        0     SÃ²lid   
3   01041301      Barri  0104130101  LÃ­mit de barri  ...        0     SÃ²lid   
4   01041301      Barri  0104130101  LÃ­mit de barri  ...        0     SÃ²lid   

  VALOR1QGIS VALOR2QGIS COL_FARCIT FCOL_DESCR FHEX_COLOR COL_DESCR HEX_COLOR7  \
0          0          0         41       NULL    #E66900      NULL    #73A88F   
1          0          0         41       NULL    #E66900      NULL    #73A88F   
2          0          0         41       NULL    #E66900      NULL    #73A88F   
3          0          0         41       NULL    #E66900      NULL    #73A88F   
4          0          0         41       NULL    #E66900      NULL    #73A88F   

                                            geometry  
0  POLYGON ((428042.1568 4579741.6635, 428051.277...  
1  POLYGON ((428820.0575000001 4580133.021500001,...  
2  POLYGON ((430162.1875 4581936.9845, 430550.104...  
3  POLYGON ((431189.9074999997 4581851.4475, 4313...  
4  POLYGON ((432798.7341 4582081.2599, 432805.852...  

[5 rows x 47 columns]

In [15]:
neighboorhoods.dtypes

ID_ANNEX       object
ANNEXDESCR     object
ID_TEMA        object
TEMA_DESCR     object
ID_CONJUNT     object
CONJ_DESCR     object
ID_SUBCONJ     object
SCONJ_DESC     object
ID_ELEMENT     object
ELEM_DESCR     object
NIVELL         object
NDESCR_CA      object
NDESCR_ES      object
NDESCR_EN      object
TERME          object
DISTRICTE      object
BARRI          object
AEB            object
SEC_CENS       object
GRANBARRI      object
ZUA            object
AREA_I         object
LITERAL        object
PERIMETRE     float64
AREA          float64
ORD_REPRES      int64
CODI_UA        object
TIPUS_UA       object
NOM            object
WEB1           object
WEB2           object
WEB3           object
DOCUMENTA      object
RANGESCALA     object
TIPUS_POL      object
GRUIX_ID       object
GRUIXDIMEN    float64
ESTIL_ID       object
ESTIL_QGIS     object
VALOR1QGIS     object
VALOR2QGIS     object
COL_FARCIT     object
FCOL_DESCR     object
FHEX_COLOR     object
COL_DESCR      object
HEX_COLOR7

In [16]:
import folium

mapi = folium.Map(location=[barcelona_stations.Latitude.mean(), barcelona_stations.Longitude.mean()], 
                  zoom_start=11,
                  control_scale = True)
folium.TileLayer('cartodbpositron', attr='igs').add_to(mapi)

folium.GeoJson(
    neighboorhoods,
    style_function=lambda feature: {
        #'fillColor': 'green' if 'l' in feature['properties']['NOMBRE'].lower() else '#ffff00',
        'color': 'black',
        'weight': 1,
        'dashArray': '5, 5',
        'fillOpacity': 0.1
    }
).add_to(mapi)

mapi

# Poblation

In [17]:
#scraping the tables from the web
tables = pd.read_html('https://www.bcn.cat/estadistica/castella/dades/inf/lecpadro/lec19/t13.htm', header=4)

In [18]:
poblacion = tables[0]
#clean the data
poblacion = poblacion.iloc[4:77]
poblacion = poblacion[[poblacion.columns[0],poblacion.columns[4]]]
poblacion

Dto. Barrios   TOTAL
4                                       1 1. el Raval  48.297
5                                 1 2. el Barri Gòtic  19.180
6                                 1 3. la Barceloneta  15.173
7          1 4. Sant Pere, Santa Caterina i la Ribera  23.170
8                                  2 5. el Fort Pienc  32.649
9                             2 6. la Sagrada Família  51.911
10                        2 7. la Dreta de l'Eixample  44.215
11               2 8. l'Antiga Esquerra de l'Eixample  43.112
12                2 9. la Nova Esquerra de l'Eixample  58.642
13                                  2 10. Sant Antoni  38.566
14               3 11. el Poble Sec-AEI Parc Montjuïc  40.409
15   3 12. la Marina del Prat Vermell-AEI Zona Franca   1.199
16                            3 13. la Marina de Port  31.087
17                        3 14. la Font de la Guatlla  10.373
18                                  3 15. Hostafrancs  16.155
19                                   3 16. la Bordeta  19.443
20                                  3 17. Sants-Badal  24.474
21                                        3 18. Sants  42.310
22                                    4 19. les Corts  46.599
23                   4 20. la Maternitat i Sant Ramon  23.992
24                                    4 21. Pedralbes  12.000
25        5 22. Vallvidrera, el Tibidabo i les Planes   4.727
26                                       5 23. Sarrià  25.137
27                              5 24. les Tres Torres  16.671
28                     5 25. Sant Gervasi-la Bonanova  26.108
29                         5 26. Sant Gervasi-Galvany  47.928
30                         5 27. el Putxet i el Farró  29.875
31                    6 28. Vallcarca i els Penitents  15.902
32                                      6 29. el Coll   7.518
33                                     6 30. la Salut  13.431
..                                                ...     ...
47                8 44. Vilapicina i la Torre Llobeta  25.895
48                                        8 45. Porta  26.557
49                          8 46. el Turó de la Peira  15.825
50                                  8 47. Can Peguera   2.247
51                                 8 48. la Guineueta  15.398
52                                    8 49. Canyelles   6.884
53                                 8 50. les Roquetes  16.250
54                                       8 51. Verdun  12.578
55                               8 52. la Prosperitat  26.834
56                             8 53. la Trinitat Nova   7.620
57                                   8 54. Torre Baró   2.931
58                             8 55. Ciutat Meridiana  10.864
59                                     8 56. Vallbona   1.407
60                            9 57. la Trinitat Vella  10.337
61                                9 58. Baró de Viver   2.604
62                                9 59. el Bon Pastor  13.126
63                                  9 60. Sant Andreu  57.961
64                                   9 61. la Sagrera  29.400
65                     9 62. el Congrés i els Indians  14.557
66                                        9 63. Navas  22.279
67                  10 64. el Camp de l'Arpa del Clot  39.034
68                                     10 65. el Clot  27.172
69           10 66. el Parc i la Llacuna del Poblenou  15.713
70               10 67. la Vila Olímpica del Poblenou   9.348
71                                 10 68. el Poblenou  34.170
72  10 69. Diagonal Mar i el Front Marítim del Pob...  13.625
73                       10 70. el Besòs i el Maresme  24.660
74                     10 71. Provençals del Poblenou  21.303
75                    10 72. Sant Martí de Provençals  26.168
76                         10 73. la Verneda i la Pau  28.883

[73 rows x 2 columns]

In [19]:
poblacion[['Dto', 'Barrio']] = poblacion['Dto. Barrios'].str.split(' ',1, expand=True)
poblacion = poblacion[['Dto', 'Barrio', 'TOTAL']].rename(columns={'TOTAL':'population'})

In [20]:
poblacion[['code','neighborhood']] = poblacion['Barrio'].str.split('.',1, expand=True)

In [21]:
poblacion = poblacion[['Dto', 'code', 'neighborhood', 'population']]

In [22]:
poblacion['population'] = poblacion['population'].str.replace('.','')
poblacion

Dto code                                   neighborhood population
4    1    1                                       el Raval      48297
5    1    2                                 el Barri Gòtic      19180
6    1    3                                 la Barceloneta      15173
7    1    4          Sant Pere, Santa Caterina i la Ribera      23170
8    2    5                                  el Fort Pienc      32649
9    2    6                             la Sagrada Família      51911
10   2    7                         la Dreta de l'Eixample      44215
11   2    8                l'Antiga Esquerra de l'Eixample      43112
12   2    9                 la Nova Esquerra de l'Eixample      58642
13   2   10                                    Sant Antoni      38566
14   3   11                 el Poble Sec-AEI Parc Montjuïc      40409
15   3   12     la Marina del Prat Vermell-AEI Zona Franca       1199
16   3   13                              la Marina de Port      31087
17   3   14                          la Font de la Guatlla      10373
18   3   15                                    Hostafrancs      16155
19   3   16                                     la Bordeta      19443
20   3   17                                    Sants-Badal      24474
21   3   18                                          Sants      42310
22   4   19                                      les Corts      46599
23   4   20                     la Maternitat i Sant Ramon      23992
24   4   21                                      Pedralbes      12000
25   5   22          Vallvidrera, el Tibidabo i les Planes       4727
26   5   23                                         Sarrià      25137
27   5   24                                les Tres Torres      16671
28   5   25                       Sant Gervasi-la Bonanova      26108
29   5   26                           Sant Gervasi-Galvany      47928
30   5   27                           el Putxet i el Farró      29875
31   6   28                      Vallcarca i els Penitents      15902
32   6   29                                        el Coll       7518
33   6   30                                       la Salut      13431
..  ..  ...                                            ...        ...
47   8   44                  Vilapicina i la Torre Llobeta      25895
48   8   45                                          Porta      26557
49   8   46                            el Turó de la Peira      15825
50   8   47                                    Can Peguera       2247
51   8   48                                   la Guineueta      15398
52   8   49                                      Canyelles       6884
53   8   50                                   les Roquetes      16250
54   8   51                                         Verdun      12578
55   8   52                                 la Prosperitat      26834
56   8   53                               la Trinitat Nova       7620
57   8   54                                     Torre Baró       2931
58   8   55                               Ciutat Meridiana      10864
59   8   56                                       Vallbona       1407
60   9   57                              la Trinitat Vella      10337
61   9   58                                  Baró de Viver       2604
62   9   59                                  el Bon Pastor      13126
63   9   60                                    Sant Andreu      57961
64   9   61                                     la Sagrera      29400
65   9   62                       el Congrés i els Indians      14557
66   9   63                                          Navas      22279
67  10   64                     el Camp de l'Arpa del Clot      39034
68  10   65                                        el Clot      27172
69  10   66              el Parc i la Llacuna del Poblenou      15713
70  10   67                  la Vila Olímpica del Poblenou       9348
71  10   68                                    el Poblenou      34170
72  10   69  

In [23]:
neigh = gp.GeoDataFrame(pd.merge(neighboorhoods[['BARRI','geometry']].astype({'BARRI':'int32'}),
                                 poblacion.astype({'code':'int32'}), 
                                 left_on='BARRI', 
                                 right_on='code').astype({'population':'int32'}),
                       geometry='geometry',
                       crs='EPSG:25831')


In [24]:
neigh.crs

'EPSG:25831'

In [25]:
neigh['density'] = neigh['population'] / (neigh.area/1000)

In [27]:
mapi = folium.Map(location=[barcelona_stations.Latitude.mean(), barcelona_stations.Longitude.mean()], 
                  zoom_start=12,
                  control_scale = True)
folium.TileLayer('cartodbpositron', attr='igs').add_to(mapi)


choropleth = folium.Choropleth(
    geo_data=neigh,
    data=neigh[['code','density']],
    columns=['code','density'],
    key_on='feature.properties.code',
    fill_color='YlGn',
    legend_name='density (inhabitats per square km)',
    highlight=True
).add_to(mapi)


choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(['density','neighborhood'])
)


for lat, lon, poi, line in zip(barcelona_stations['Latitude'], 
                                  barcelona_stations['Longitude'], 
                                  barcelona_stations['station'], 
                                  barcelona_stations['line']):
    label = folium.Popup(str(poi) + ' Line ' + str(line), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=2,
        popup=label,
        color='blue',
        fill=True,
        fill_color='blue',
        fill_opacity=0.7).add_to(mapi)
       
mapi


mapi

neigh

### Saving data

In [29]:
neigh.to_file("barcelona_neigh.shp")
# save
barcelona_stations.to_csv('metro_barcelona_uniques.csv')

In [35]:
print(barcelona_stations.shape)
print(neigh.shape)

(230, 7)
(73, 7)


Represent only barcelona stations

In [30]:
#shape of barcelona
barcelona = neigh.geometry.unary_union

In [31]:
neigh.crs

'EPSG:25831'

In [33]:
geo_stations = gp.GeoDataFrame(
     barcelona_stations, geometry=gp.points_from_xy(barcelona_stations['Longitude'], barcelona_stations['Latitude']))
#this coordinates are in epsg:4326 we need them with the same as neigh
geo_stations.crs = {'init': 'epsg:4326'}
geo_stations = geo_stations.to_crs(epsg=25831)

In [36]:
geo_stations.shape

(230, 7)

In [37]:
stations_only_barcelona = barcelona_stations[geo_stations.within(barcelona)]
print(stations_only_barcelona.shape)

(144, 7)


In [38]:
mapi = folium.Map(location=[barcelona_stations.Latitude.mean(), barcelona_stations.Longitude.mean()], 
                  zoom_start=12,
                  control_scale = True)
folium.TileLayer('cartodbpositron', attr='igs').add_to(mapi)


choropleth = folium.Choropleth(
    geo_data=neigh,
    data=neigh[['code','density']],
    columns=['code','density'],
    key_on='feature.properties.code',
    fill_color='YlGn',
    legend_name='density (inhabitats per square km)',
    highlight=True
).add_to(mapi)


choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(['density','neighborhood'])
)


for lat, lon, poi, line in zip(stations_only_barcelona['Latitude'], 
                                  stations_only_barcelona['Longitude'], 
                                  stations_only_barcelona['station'], 
                                  stations_only_barcelona['line']):
    label = folium.Popup(str(poi) + ' Line ' + str(line), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=2,
        popup=label,
        color='blue',
        fill=True,
        fill_color='blue',
        fill_opacity=0.7).add_to(mapi)
       
mapi


mapi